In [1]:
from imports import *
import traces_rdf
%matplotlib inline

Welcome to JupyROOT 6.28/10


In [2]:
FastTempl = 'data/TES_TwoTemplate/FastDMC-lite_00240606_0000.root'
Fast2T = 'data/TES_TwoTemplate/FastDMC-2T_00240702_0000.root'
Fast2Trs = 'data/TES_TwoTemplate/FastDMC-2Trs_00240811_0000.root'
Narrow2T = 'data/TES_TwoTemplate/FastDMC-2T-narrow_00240702_0000.root'
Scaled2T = 'data/TES_TwoTemplate/FastDMC-2Tra-scaled_00240628_0000.root'
lite1801 = 'data/TES_TwoTemplate/cdmslite-ODE-elog1801_51240702_0000.root'
lite12_01 = 'data/TES_TwoTemplate/cdmslite-ODE-V12-01-00_51240626_0000.root'
lite12_04 = 'data/TES_TwoTemplate/cdmslite-ODE-V12-04-00_51240626_0000.root'
lite13_00 = 'data/TES_TwoTemplate/cdmslite-ODE-V13-00-00_51240626_0000.root'
centerODE = 'data/TES_TwoTemplate/cdmslite-ODE-center_51240702_0000.root'
center2T = 'data/TES_TwoTemplate/FastDMC-2T-center_00240702_0000.root'
ptof2T = 'data/TES_TwoTemplate/FastDMC-2T-ptof_00240703_0000.root'
aScale2T = 'data/TES_TwoTemplate/FastDMC-2T-aScale_00240706_0000.root'

# ---------------------------------------------------------------------------------------------
# Event Number of Interest
event = 0
timeRange = [-800, 6400.]     # Used for all the plots below

In [3]:
# Page of four channel plots or overlays
def tracePage(files, names="", event=0, descr=""):
    """Generate a set of four plots for the CDMSlite channels, reading traces from
       the listed files.  'files' can be a single filename, a list, or a dictionary
       with a descriptive name for each file as a key.  The descriptive name(s) may
       be passed separately.

       Typical usage: tracePage(files...).savefig("filename.png")
       """
    
    if isinstance(files, dict):     # User can supply name/file dictionary directly
        fileset = files
    else:                           # Create dictionary from separate lists
        if isinstance(files, str): files = [files]
        if isinstance(names, str): names = [names]
        fileset = dict(zip(names,files))
    
    fig, axes = subplots(2,2,figsize=(9,6), dpi = 1000)
    fig.set_tight_layout(True)
    chans = ["PA", "PB", "PC", "PD"]

    for plot in range(4):
        currentAxis = axes.flatten()[plot]

        # Overlay each channel trace from all of the input files
        i = -1
        for name,file in fileset.items():
            i += 1    # Use this for the colors
            bins, trace, _,_ = traces_rdf.getTES(file, event, plot)
            currentAxis.plot(bins, trace, lw=1, color=f"C{i}", label=name)

        currentAxis.set_xlim(timeRange)
        currentAxis.set_xlabel("Time [\u03BCs]")
        currentAxis.set_ylabel("Trace [\u03BCA]")
        currentAxis.set_title(f"{descr} CDMSlite {chans[plot]}")
        if (len(fileset)>1): currentAxis.legend(loc="upper right")

    return fig

In [17]:
tracePage({"TES_ODE":lite1801, "2T (R,S)":Fast2Trs}).savefig("CDMSlite_2T-resid-slow.png")

In [5]:
tracePage({"TES_ODE":lite1801, "2T-ptofScale":aScale2T}).savefig("CDMSlite_2T-ptofScale.png")

In [6]:
# tracePage({"TES_ODE":lite1801, "2T-ptof":ptof2T}).savefig("CDMSlite_2Tptof.png")

In [7]:
# tracePage(FastTempl,descr="FastDMC").savefig("CDMSlite_FastDMC.png")

In [8]:
# tracePage(Fast2T, descr="2T(R,A)").savefig("CDMSlite_2Tra.png")

In [9]:
# tracePage(Narrow2T, descr="0.1mm Gaussian, 2T(R,A)").savefig("CDMSlite_2T-narrow.png")

In [10]:
# tracePage(Scaled2T, descr="2T(R,A) area-scaled").savefig("CDMSlite_2T-scaled.png")

In [11]:
# tracePage([FastTempl,Fast2T],["FastDMC","2T(R,A)"]).savefig("CDMSlite_Overlay-2T.png")

In [12]:
# tracePage({ "TES_ODE":lite1801, "2T(R,A)":Fast2T}).savefig("CDMSlite_ODE-2T.png")

In [13]:
# tracePage({ "TES_ODE":lite1801, "2T(R,A) scaled":Scaled2T}).savefig("CDMSlite_ODE-2Tscaled.png")

In [14]:
# Overlay the four TES_ODE tests of fast/slow energy
odeset = {"V12-01-00": lite12_01,
          "V12-04-00": lite12_04,
          "V13-00-00": lite13_00,
          "elog/1801": lite1801}
tracePage(odeset, descr="TES_ODE").savefig("CDMSlite_ODEversions.png")

In [18]:
branches = ["PhononE","PhononEfast","PhononEslow"]
#energyODE  = traces_rdf.convertRDFBranches(ROOT.RDataFrame("G4SimDir/g4dmcEvent",lite1801,branches).AsNumpy(branches))
energy2T = traces_rdf.convertRDFBranches(ROOT.RDataFrame("G4SimDir/g4dmcEvent",Fast2Trs,branches).AsNumpy(branches))
eCenter2T  = traces_rdf.convertRDFBranches(ROOT.RDataFrame("G4SimDir/g4dmcEvent",center2T,branches).AsNumpy(branches))

In [24]:
energy2T['PhononEavg'] = energy2T['PhononEslow']
energy2T['avgEfast'] = [[sum(energy2T['PhononEfast'])/4 for i in range(4)]]
energy2T['PhononEresid'] = energy2T['PhononE']-energy2T['avgEfast']

IvsE = 51.52e-6 # uA/eV, for CDMSlite1
Aratio = 8.00724
energy2T["DMCPamps"] = energy2T["PhononEavg"] * IvsE
energy2T["DMCRamps"] = energy2T["PhononEresid"] * IvsE * Aratio

energy2T

{'PhononE': array([[28604.06962265, 29161.81560235, 34669.12941543, 29219.28535957]]),
 'PhononEfast': array([[1306.70593681, 1864.4519165 , 7371.76572958, 1921.92167373]]),
 'PhononEslow': array([[27297.36368585, 27297.36368585, 27297.36368585, 27297.36368585]]),
 'PhononEavg': array([[27297.36368585, 27297.36368585, 27297.36368585, 27297.36368585]]),
 'avgEfast': [[3116.211314154056,
   3116.211314154056,
   3116.211314154056,
   3116.211314154056]],
 'PhononEresid': array([[25487.8583085 , 26045.60428819, 31552.91810127, 26103.07404542]]),
 'DMCPamps': array([[1.40636018, 1.40636018, 1.40636018, 1.40636018]]),
 'DMCRamps': array([[10.51458277, 10.7446714 , 13.01662011, 10.76837957]])}

In [ ]:
eCenterODE['PhononEavg'] = [[sum(eCenterODE['PhononE'])/4 for i in range(4)]]
eCenterODE['PhononEresid'] = eCenterODE['PhononE']-eCenterODE['PhononEavg']
eCenterODE

In [ ]:
eCenter2T['PhononEavg'] = [[sum(eCenter2T['PhononE'])/4 for i in range(4)]]
eCenter2T['PhononEresid'] = eCenter2T['PhononE']-eCenter2T['PhononEavg']
eCenter2T

In [ ]:
# provide file path to DMC templates files
simpath   = os.path.join(os.environ["CDMS_SUPERSIM"], "CDMSgeometry", "data", "dmc", "CDMSlite1")
templ1T   = os.path.join(simpath, "TESTemplates")
templFast = os.path.join(simpath, "TESTemplatesFast")
templSlow = os.path.join(simpath, "TESTemplatesSlow")

In [ ]:
# Load templates file into Pandas dataframe (copied from Rik_FETTemplates.ipynb)
def loadTemplate(file):
    df=pd.read_csv(file,sep="\t")  # header = 0 , sep = "," are default
    print(df)

    for index in range(1):
    
        Sigchan_iZIP5=df.loc[9,"Sigchan"]
        print(Sigchan_iZIP5)

    row0=df.loc[0,"Trace"].split()
    a=[float(x) for x in row0]

    b=[i for i in a if i != 0.0]
    nBin=(len(a))